In [14]:
# Import required libraries
import requests
import pandas as pd
from urllib.parse import urlencode, urlunparse
from pprint import pprint
import json
import os
from sqlalchemy import create_engine, text, Column, Float, String, DateTime
import pymssql



In [5]:
## Creating URL to fetch data for a single coordinate
# Base URL and parameters
base_url = "https://api3.geo.admin.ch/rest/services/api/MapServer/identify"
params = {
    "geometryType": "esriGeometryPoint",
    "returnGeometry": "false",
    "sr": "4326",  # Spatial reference system WGS84
    "imageDisplay": "0,0,0",
    "mapExtent": "0,0,0,0",
    "tolerance": "0",
    "layers": "all:ch.swisstopo-vd.geometa-gemeinde"
}

# Single coordinate (longitude, latitude)
coordinate = (8.5220, 47.5762)

params["geometry"] = f"{coordinate[0]},{coordinate[1]}"
    
# Build the full URL with the updated parameters
query_string = urlencode(params)
full_url = f"{base_url}?{query_string}"
    
print(f"Requesting URL: {full_url}")

Requesting URL: https://api3.geo.admin.ch/rest/services/api/MapServer/identify?geometryType=esriGeometryPoint&returnGeometry=false&sr=4326&imageDisplay=0%2C0%2C0&mapExtent=0%2C0%2C0%2C0&tolerance=0&layers=all%3Ach.swisstopo-vd.geometa-gemeinde&geometry=8.522%2C47.5762


In [6]:
# Function to fetch data for a single coordinate
def get_location_info(lon, lat):
    # Update the geometry in parameters with the provided coordinate
    params["geometry"] = f"{lon},{lat}"
    
    # Build the full URL with the updated parameters
    query_string = urlencode(params)
    full_url = f"{base_url}?{query_string}"
    
    print(f"Requesting URL: {full_url}")
    
    # Send the request
    response = requests.get(full_url)
    
    # Return the JSON response
    return response.json()

In [11]:
# Fetch and print location information for the coordinate
location_data = get_location_info(*coordinate)
pprint(location_data)

Requesting URL: https://api3.geo.admin.ch/rest/services/api/MapServer/identify?geometryType=esriGeometryPoint&returnGeometry=false&sr=4326&imageDisplay=0%2C0%2C0&mapExtent=0%2C0%2C0%2C0&tolerance=0&layers=all%3Ach.swisstopo-vd.geometa-gemeinde&geometry=8.522%2C47.5762
{'results': [{'attributes': {'abgabestelle': 'maps.zh.ch?topic=AVfarbigZH&locate=gemeinden&locations=55',
                             'bfs_nr': 55,
                             'bgdi_created': '21.11.2024',
                             'fid': '55',
                             'flaeche_ha': '906',
                             'gemeindename': 'Eglisau',
                             'kanton': 'Zürich',
                             'label': 'Eglisau',
                             'pdf_liste': 'http://geodata01.admin.ch/meta/av/0055_l1_de.pdf;http://geodata01.admin.ch/meta/av/0055_l1_fr.pdf;http://geodata01.admin.ch/meta/av/0055_l1_it.pdf'},
              'featureId': 329,
              'id': 329,
              'layerBodId':

### Connect to SQL-DB and get all required coordinates

In [15]:
# Load database access configuration from config/db_config.json
with open('../config/db_config.json', 'r') as f:
    db_config = json.load(f)

# Access db credentials
server = db_config['server']
database = db_config['database']
db_user = db_config['db_user']
db_password = db_config['db_password']

In [16]:
# Connect to SQL Database
conn = pymssql.connect(server, db_user, db_password, database)

# Create connection string for SQLAlchemy
connection_string = f"mssql+pymssql://{db_user}:{db_password}@{server}/{database}"
engine = create_engine(connection_string)

In [18]:
# Read data from SQL table about hiking trails and print the first rows
df_HikingRoutes = pd.read_sql_table(table_name='OVRP_HikingRoutes', con=engine)
print(df_HikingRoutes.head(8))

       id                               name                  symbol  \
0  120125  Les Cernets Dessus-Pouetta Raisse  yellow::yellow_diamond   
1  121950            Ober Loh - Untere Alpli  yellow::yellow_diamond   
2  121951         Untere Alpli - Obere Alpli  yellow::yellow_diamond   
3  121952            Unter Alpli - Schwämmli  yellow::yellow_diamond   
4  121955       Obere Tweralp-Untere Tweralp       red:white:red_bar   
5  121956            Untere Tweralp-Bodenwis  yellow::yellow_diamond   
6  121958             Gebertingerwald-Ricken  yellow::yellow_diamond   
7  135975             Hadlikon - Breitenmatt  yellow::yellow_diamond   

        von          bis        lat       lon   timestamp_apicall  
0      None         None  46.860941  6.614409 2024-11-20 20:49:42  
1      None         None  47.320476  9.032205 2024-11-20 20:49:42  
2      None         None  47.313913  9.034028 2024-11-20 20:49:42  
3      None         None  47.309656  9.030998 2024-11-20 20:49:42  
4      None

In [51]:
# Extract unique coordinates from dataframe
df_Coords = df_HikingRoutes[['id', 'lat', 'lon']].drop_duplicates(subset=['id','lat', 'lon'], keep='first')
print(df_Coords.head(5))
print("------------------------")
print(df_Coords.info())

       id        lat       lon
0  120125  46.860941  6.614409
1  121950  47.320476  9.032205
2  121951  47.313913  9.034028
3  121952  47.309656  9.030998
4  121955  47.291579  9.028361
------------------------
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2970 entries, 0 to 2969
Data columns (total 3 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   id      2970 non-null   int64  
 1   lat     2970 non-null   float64
 2   lon     2970 non-null   float64
dtypes: float64(2), int64(1)
memory usage: 69.7 KB
None


In [52]:
# Get current working directory
current_dir = os.getcwd()
print(current_dir)

# c:\Users\etien\OneDrive\02_Progression\CAS_DataEngineering_ZHAW\03_Leistungsnachweis\Wanderwege\notebooks

c:\Users\etien\OneDrive\02_Progression\CAS_DataEngineering_ZHAW\03_Leistungsnachweis\Wanderwege\notebooks


### Fetch all addresses for the given coordinates

In [69]:
# Initialize the results list to store coordinates, location data, and their attributes
results = []
location_data_list = []  # This will store the full dataset fetched from the API

# Set the maximum number of coordinates to process (e.g., 10 for testing)
#max_coordinates = 10

# Process each coordinate from the DataFrame and fetch data
for i, (_, row) in enumerate(df_Coords.iterrows(), start=1):
    #if i > max_coordinates:  # Stop once the max number of coordinates is processed
    #    break
    
    id, lon, lat = row['id'], row['lon'], row['lat']
    
    # Print the current coordinate being processed
    print(f"Processing coordinate {i}: ID = {id}, Longitude = {lon}, Latitude = {lat}")
    
    # Fetch location data for the current coordinate
    location_data = get_location_info(lon, lat)
    
    # Print a message when the data is fetched
    print(f"Fetched data for id and coordinate {i}: {id} - {location_data}")
    
    # Store the full location data
    location_data_list.append(location_data)
    
    # Initialize variables to None (in case there are no results)
    gemeindename = None
    kanton = None
    
    # Check if there are results before trying to extract data
    if location_data["results"]:
        gemeindename = location_data["results"][0]["attributes"].get("gemeindename", None)
        kanton = location_data["results"][0]["attributes"].get("kanton", None)
    
    # Store the extracted data in the results list for the DataFrame
    results.append({
        "id": id,
        "lat": lat,
        "lon": lon,
        "gemeindename": gemeindename,
        "kanton": kanton
    })

# Convert the results list into a pandas DataFrame
df_addresses = pd.DataFrame(results)

# Add time and datestamp of API call to dataframe
timestamp_apicall = pd.Timestamp.now().strftime("%Y-%m-%d %H:%M:%S")
df_addresses['timestamp_apicall'] = timestamp_apicall


Processing coordinate 1: ID = 120125.0, Longitude = 6.6144089, Latitude = 46.8609414
Requesting URL: https://api3.geo.admin.ch/rest/services/api/MapServer/identify?geometryType=esriGeometryPoint&returnGeometry=false&sr=4326&imageDisplay=0%2C0%2C0&mapExtent=0%2C0%2C0%2C0&tolerance=0&layers=all%3Ach.swisstopo-vd.geometa-gemeinde&geometry=6.6144089%2C46.8609414
Fetched data for id and coordinate 1: 120125.0 - {'results': [{'layerBodId': 'ch.swisstopo-vd.geometa-gemeinde', 'layerName': 'Gemeindeinformationen - AV', 'featureId': 105, 'id': 105, 'attributes': {'fid': '5562', 'gemeindename': 'Mauborget', 'kanton': 'Vaud', 'flaeche_ha': '551', 'bfs_nr': 5562, 'pdf_liste': 'http://geodata01.admin.ch/meta/av/5562_l1_de.pdf;http://geodata01.admin.ch/meta/av/5562_l1_fr.pdf;http://geodata01.admin.ch/meta/av/5562_l1_it.pdf', 'abgabestelle': 'www.geo.vd.ch/?&mapresources=GEOVD_MENSURATION', 'bgdi_created': '21.11.2024', 'label': 'Mauborget'}}]}
Processing coordinate 2: ID = 121950.0, Longitude = 9.03

In [71]:
# Optionally, print the DataFrame to check the result
print("\nResults DataFrame:")
print(df_addresses)

# Optionally, print the full location data stored in the list
print("\nFull Location Data:")
pprint(location_data_list)


Results DataFrame:
              id        lat       lon gemeindename      kanton  \
0       120125.0  46.860941  6.614409    Mauborget        Vaud   
1       121950.0  47.320476  9.032205      Mosnang  St. Gallen   
2       121951.0  47.313913  9.034028      Mosnang  St. Gallen   
3       121952.0  47.309656  9.030998      Mosnang  St. Gallen   
4       121955.0  47.291579  9.028361      Wattwil  St. Gallen   
...          ...        ...       ...          ...         ...   
2965  18260272.0  47.711211  8.873704         None        None   
2966  18260273.0  47.712326  8.874469         None        None   
2967  18260275.0  47.713105  8.874250         None        None   
2968  18260276.0  47.713656  8.882556         None        None   
2969  18260277.0  47.709821  8.888222         None        None   

        timestamp_apicall  
0     2024-11-21 22:40:49  
1     2024-11-21 22:40:49  
2     2024-11-21 22:40:49  
3     2024-11-21 22:40:49  
4     2024-11-21 22:40:49  
...                

In [72]:
# Create table in sql dabase if it doesn't exist and ingest data
table_name = "GEOA_Addresses"
query = f"""
    IF OBJECT_ID(N'dbo.{table_name}', N'U') IS NULL
    BEGIN
        CREATE TABLE {table_name} (
            id                          INT                 NOT NULL,
            lat                         FLOAT               NOT NULL,
            lon                         FLOAT               NOT NULL,
            gemeindename                VARCHAR(255)        NULL,
            kanton                      VARCHAR(255)        NULL,
            timestamp_apicall           DATETIME            NULL,
            
            PRIMARY KEY (id)
        );
    END
    """

# Connect to SQL Database
conn = pymssql.connect(server, db_user, db_password, database)
cursor = conn.cursor()

# Execute query
cursor.execute(query)

conn.commit()
conn.close()

In [73]:
# Create connection string for SQLAlchemy
connection_string = f"mssql+pymssql://{db_user}:{db_password}@{server}/{database}"
engine = create_engine(connection_string)

In [74]:
# Write data to database and replace existing table
df_addresses.to_sql(table_name, con=engine, if_exists='replace', index=False)

178